# Lecture 3: Gaussian Elimination and LU Factorization

In this demonstration, we want to show you:

* Why triangular matrices are useful
* How to perform Gaussian elimination
* How to code elementary row operations

In [1]:
import numpy as np

## First step of Gaussian elimination

Linear systems that have special forms (namely, upper triangular
and lower triangular systens) can be solved using the method
of repeated substitution instead of using more complicated
machinery. Note that repeated substitution is not a new
concept to you, you have already learned this in linear
algebra, we are just putting it into code.

Before we get to implementing and kind of repeated substitution, we should
make a function that can perform Gaussian elimination
on a system to convert it to this special $U \vec{x} = \vec{b}$
form. Recall that Gaussian elimination has the form:

1. Eliminate all leading coefficients in rows below the top
row using elementary row operations.
2. Perform Gaussian elimination on the new system without
the left-most column and upper-most row.
3. Stop when you are performing Gaussian elimination on
a system of 1 variable.

Instead of tackling Gaussian elimination as a whole, we can
write a helper function that performs step 1 for us:

In [2]:
def eliminate(A, b, k):
    """Eliminate leading coefficients in the rows below the k-th row of A
    in the system np.matmul(A, x) == b. The elimination is done in place."""
    n = A.shape[0]
    for i in range(k + 1, n): # loop through rows below row k
        m = A[i, k] / A[k, k] # find the factor needed to eliminate the leading coefficient
        A[i, :] = A[i, :] - m * A[k, :] # perform the elementary row operation to eliminate leading coefficient
        b[i] = b[i] - m * b[k] # we need to perform the operation on b as well

Let's see an example of this elimination being done:

In [3]:
A = np.array([
    [1, 2, 3],
    [4, 5, 6],
    [7, 8, 8]
])
b = np.array([1, 1, 1])

eliminate(A, b, 0) # eliminate leading coefficients in all rows below the top row

print(A)
print(b)

[[  1   2   3]
 [  0  -3  -6]
 [  0  -6 -13]]
[ 1 -3 -6]


Let's compare the result of the `eliminate` function with what we would expect
by doing the elimination by hand:

$A = \begin{bmatrix}1 & 2 & 3 \\ 4 & 5 & 6 \\ 7 & 8 & 8 \end{bmatrix}, \vec{b} = \begin{bmatrix}1 \\ 1 \\ 1 \end{bmatrix}$
$R_2 \longrightarrow R_2 - 4R_1$
$A = \begin{bmatrix}1 & 2 & 3 \\ 0 & -3 & -6 \\ 7 & 8 & 8 \end{bmatrix}, \vec{b} = \begin{bmatrix}1 \\ -3 \\ 1 \end{bmatrix}$
$R_3 \longrightarrow R_3 - 7R_1$
$A = \begin{bmatrix}1 & 2 & 3 \\ 0 & -3 & -6 \\ 0 & -6 & -13 \end{bmatrix}, \vec{b} = \begin{bmatrix}1 \\ -3 \\ -6 \end{bmatrix}$

So now we know that `eliminate` does what we expect it to do, we can use it in a Gaussian
elimination function.

## Second step of Gaussian elimination

Luckily for us, the `eliminate` function was the hardest part of implementing
Gaussian elimination. All we have to do is call the `eliminate` function
recursively on the system without the left-most column and upper-most row!
Note that we must redefine `A` and `b` because our `eliminate` function works
on them in place:

In [4]:
A = np.array([
    [1, 2, 3],
    [4, 5, 6],
    [7, 8, 8]
])
b = np.array([1, 1, 1])

def gauss_elimination(A, b):
    """Convert the system np.matmul(A, x) == b into the equivalent system np.matmul(U, x) == c
    via Gaussian elimination. The elimination is done in place."""
    if A.shape[0] == 1:
        return
    eliminate(A, b, 0)
    gauss_elimination(A[1:, 1:], b[1:])

Instead of looking at the result of calling `gauss_elimination(A, b)`, let's finish the
elimination we did by hand in the first part and then compare results:

$A = \begin{bmatrix}1 & 2 & 3 \\ 0 & -3 & -6 \\ 0 & -6 & -13 \end{bmatrix}, \vec{b} = \begin{bmatrix}1 \\ -3 \\ -6 \end{bmatrix}$
$R_3 \longrightarrow R_3 - 2R_2$
$A = \begin{bmatrix}1 & 2 & 3 \\ 0 & -3 & -6 \\ 0 & 0 & -1 \end{bmatrix}, \vec{b} = \begin{bmatrix}1 \\ -3 \\ 0 \end{bmatrix}$

Is this what our `gauss_elimination` function will yield? Let's find out:

In [5]:
gauss_elimination(A, b)

print(A)
print(b)

[[ 1  2  3]
 [ 0 -3 -6]
 [ 0  0 -1]]
[ 1 -3  0]


Our implementation of Gaussian elimination worked!

## Caveats

Even though our implementation of Gaussian elimination works, it does not actually
solve the linear system. In fact, the only thing our `gauss_elimination` function does
is transform our linear system into an equivalent linear system. Fortunately,
the transformed problem is **extremely** easy to solve!

You may also noteice that our `gauss_elimination` function does not work on some
matrices that are well conditioned. This can be because of a loss of precision
in some floating point computations. This effect can be reduced using a method 
called **pivoting**, you will learn about this in the lecture next week!